In [116]:
import random
import math
import agentpy as ap
import numpy as np
# Visualization
import seaborn as sns
import pandas as pd
import matplotlib.pyplot as plt
import IPython

In [117]:
class RandomAgent(ap.Agent):
    """ Se mueve a celdas al azar """
    
    def setup(self):
        self.position = (0,0)  # Posición actual del agente (x, y)
        self.intention = None  # Intención actual (clean, move o wait)
        self.new_position = None  # Objetivo al moverse (x, y)
        self.is_dirty = False
        
    def see(self):
        """ Percibe su entorno """
        x, y = self.position
        self.is_dirty = self.model.is_dirty[x][y]
        self.neighbors = self.model.get_neighbors(x, y) 
    
    def next(self):
        """ Decide la próxima acción según lo que percibe """
        self.intention = "wait" # por defecto espera
        if self.is_dirty:
            self.intention = "clean"
        else:
            self.new_position = random.choice(self.neighbors)
            if self.model.is_valid_position(self.new_position):
                self.intention = "move"
                
    def action(self):
        """ Ejecuta la accion """
        x, y = self.position
        if self.intention == "clean":
            self.model.clean_cell(x, y)
        elif self.intention == "move":
            self.position = self.new_position
            
    def move(self):
        if not self.model.is_board_clean:
            self.model.total_moves += 1     
        self.see()
        self.next()
        self.action()

        

In [118]:
class SergioAgent(ap.Agent):
    """ Empieza con una estrategia de llenado en columnas, seguido de busqueda por barrido """
    
    def setup(self):
        self.position = (0,0)  # Posición actual del agente (x, y)
        self.intention = None  # Intención actual (clean, move o wait)
        self.new_position = None  # Objetivo al moverse (x, y)
        self.is_dirty = False
        self.x_dir = 1
        self.y_dir = 1
        self.is_sharing_space = False
        self.changed_dir = 0
        self.delay = 1
        
        
        # TODO: Agregar metrica de utilidad

        
    def see(self):
        """ Percibe su entorno """
        x, y = self.position
        self.is_dirty = self.model.is_dirty[x][y] 

        self.is_sharing_space = 0
        for agent in self.model.all_agents:
            if agent.position == self.position:
                self.is_sharing_space += 1
                if self.is_sharing_space > 1:
                    break
        
        # Removing itself!
        self.is_sharing_space -= 1
        
        x_max = len(self.model.is_dirty) - 1
        y_max = len(self.model.is_dirty[0]) - 1
        if x == 0 and x == x_max:
            self.x_dir = 0
        elif x == 0 and self.x_dir != 1: 
            self.x_dir = 1
            # raise RuntimeError
        elif x == x_max:
            self.x_dir = -1
        
        if y == 0 and y == y_max:
            self.y_dir = 0
        elif y == 0 and self.y_dir != 1 and self.delay <= 0:
            self.changed_dir = 1
            self.y_dir = 1
        elif y == y_max and self.y_dir != -1 and self.delay <= 0:
            self.changed_dir = 1
            self.y_dir = -1
        
        # Prevents double change in dir, just after moving to next column
        self.delay -= 1
            
            
    
    def next(self):
        """ Decide la próxima acción según lo que percibe """
        self.intention = "wait" # por defecto espera
        if self.is_dirty:
            self.delay = 1
            self.intention = "clean"
            return  
        
        x, y = self.position
        if self.changed_dir:
            self.new_position = (x + self.x_dir, y)
            self.changed_dir = 0
            self.delay = 1
        elif self.is_sharing_space:
            # algunos sigue barriendo vertical, otros se mueve horizontal
            possible_moves = [(x + self.x_dir, y), (x, y + self.y_dir)]
            index = np.random.choice([0, 1], p=[0.95, 0.05])
            if index == 0:
                self.delay = 1
            self.new_position = possible_moves[index]
        else: 
            self.new_position = (x, y + self.y_dir)
        
        if self.model.is_valid_position(self.new_position):
            self.intention = "move"
                
    def action(self):
        """ Ejecuta la accion """
        x, y = self.position
        if self.intention == "clean":
            self.model.clean_cell(x, y)
        elif self.intention == "move":
            self.position = self.new_position
            
    def move(self):
        if not self.model.is_board_clean:
            self.model.total_moves += 1     
        self.see()
        self.next()
        self.action()


In [119]:
class RodrigoAgent(ap.Agent):
    
    def setup(self):
        pass
        
    def see(self):
        pass 
    
    def next(self):
        pass
                
    def action(self):
       pass
            
    def move(self):
        if not self.model.is_board_clean:
            self.model.total_moves += 1     
        self.see()
        self.next()
        self.action()


In [120]:
class OscarAgent(ap.Agent):
    """ Idea: Dar mayor probabilidad de moverse a celdas que estén más lejos de los demás agentes. Asimismo, considerar celda sucia más cercana. """
    def setup(self):
        self.position = self.p.initial_position  # Posición actual del agente (x, y)
        self.intention = None  # Intención actual (clean o move)
        self.new_position = None  # Objetivo al moverse ([-1 | 0 | 1], [-1 | 0 | 1])
        self.is_dirty = False
        self.cleaned_cells = 0
        self.initial_dirty_cells = self.model.dirty_cells
        self.closest_factor = 0.5
        
    def see(self):
        """Considerar celdas sin limpiar y otros agentes."""
        if self.model.is_dirty[self.position[0]][self.position[1]]:
            self.is_dirty = True
        else:
            self.is_dirty = False
            self.dirty_cells =  []
            
            for i in range(len(self.model.is_dirty)):
                for j in range(len(self.model.is_dirty[i])):
                    if self.model.is_dirty[i][j]:
                        self.dirty_cells.append((i,j))
            
            self.agent_locations = [agent.position for agent in self.model.all_agents]

    def point_distance(self, p1, p2):
        return abs(p1[0] - p2[0]) + abs(p1[1] - p2[1])
    # O( celdas sucias * agentes)
    def next(self):
        if self.is_dirty:
            self.intention = "clean"
        else:
            self.intention = "move"
            self.distances = [0] * len(self.dirty_cells)
            closest_index = 0
            self.total_distance = 0
            ignored_self = False
            
            for i in range(len(self.dirty_cells)):
                if self.point_distance(self.position, self.dirty_cells[i]) < self.point_distance(self.position, self.dirty_cells[closest_index]):
                    closest_index = i

                for agent in self.agent_locations:
                    if self.position[0] == agent[0] and self.position[1] == agent[1] and not ignored_self:
                        # No considerar la posicion actual del agente, para evitar que todos los agentes tengan las mismas probabilidades
                        ignored_self = True
                    else:
                        distance = abs(self.dirty_cells[i][0] - agent[0] + self.dirty_cells[i][1] - agent[1])
                        
                        self.distances[i] += distance
                        self.total_distance += distance
            
            probabilities = [0] * len(self.dirty_cells)
            
            # Evitar division por cero
            if self.total_distance == 0:
                self.total_distance = 1
                
            for i in range(len(self.dirty_cells)):
                probabilities[i] = self.distances[i] / self.total_distance
                
            # Considerar la celda sucia más cercana
            probabilities = [p * (1 - self.closest_factor) for p in probabilities]
            
            probabilities[closest_index] += self.closest_factor
            
            for i in range(len(self.dirty_cells)):
                if self.dirty_cells[i][0] == self.position[0] and self.dirty_cells[i][1] == self.position[1]:
                    probabilities[i] += self.closest_factor
            
            # Normalizar probabilidades en caso necesario
            if not np.isclose(sum(probabilities), 1.0):
                normalization_factor = sum(probabilities)
                probabilities = [p / normalization_factor for p in probabilities]
            
            
            
            # Elegir la celda objetivo considerando las probabilidades
            try:
                target_position_index = np.random.choice([*range(len(self.dirty_cells))], p=probabilities)
            except ValueError:
                # Si hay algun error, elegir una celda al azar
                target_position_index = np.random.choice([*range(len(self.dirty_cells))])
                
            target_position = self.dirty_cells[target_position_index]
            # Obtener movimiento necesario para llegar a la celda objetivo
            x = np.sign(target_position[0] - self.position[0])
            y = np.sign(target_position[1] - self.position[1])
            
            self.new_position = (x, y)
                
    def action(self):
        """ Ejecuta la accion """
        x, y = self.position
        if self.intention == "clean":
            self.model.clean_cell(x, y)
        elif self.intention == "move":
            dx, dy = self.new_position
            self.position = (x + dx, y + dy)
    
    def utility(self):
        return self.cleaned_cells / self.initial_dirty_cells * 100
            
    def move(self):
        if not self.model.is_board_clean:
            self.model.total_moves += 1     
            self.see()
            self.next()
            self.action()


In [121]:
class PepeAgent(ap.Agent):
    
    def setup(self):
        pass
        
    def see(self):
        pass 
    
    def next(self):
        pass
                
    def action(self):
       pass
            
    def move(self):
        if not self.model.is_board_clean:
            self.model.total_moves += 1     
        self.see()
        self.next()
        self.action()


In [122]:
class HectorAgent(ap.Agent):
    
    def setup(self):
        pass
        
    def see(self):
        pass 
    
    def next(self):
        pass
                
    def action(self):
       pass
            
    def move(self):
        if not self.model.is_board_clean:
            self.model.total_moves += 1     
        self.see()
        self.next()
        self.action()


In [123]:
class CleaningModel(ap.Model):
    """ Modelo de limpieza de tablero """
    
    def generateDirtyCells(self):
        """
        Genera una matriz n x m donde un porcentaje de las celdas están marcadas como sucias (1) y el resto limpias (0).
        devuelve: Matriz n x m con celdas sucias y limpias
        """
        totalCells = self.p.n * self.p.m
    
        dirtyCellsCount = math.ceil(totalCells * (self.p.percentage_dirty / 100))

        # Inicializamos la matriz con ceros
        isDirty = [[0 for _ in range(self.p.m)] for _ in range(self.p.n)]

        # Generamos las posiciones de las celdas sucias de manera aleatoria
        allPositions = [(i, j) for i in range(self.p.n) for j in range(self.p.m)]
        dirtyPositions = random.sample(allPositions, dirtyCellsCount)

        # Marcamos las celdas seleccionadas como sucias
        for i, j in dirtyPositions:
            isDirty[i][j] = 1

        return isDirty
    
    def is_valid_position(self, position):
        """ Verifica si una posición es valida dentro de nuestro tablero """
        x, y = position
        return 0 <= x < self.p.n and 0 <= y < self.p.m
    
    def get_neighbors(self, x, y):
        """ regresa lista con todas las celdas vecinas de la posicion x, y"""
        neighbors = []
        
        for dx in range(-1, 2):  # Iterata -1, 0, 1
            for dy in range(-1, 2):  # Itera -1, 0, 1
                if not (dx == 0 and dy == 0):  # Saltamos la celda actual
                    neighbors.append((x + dx, y + dy)) 
    
        return neighbors
    
    def clean_cell(self, x, y): 
        if self.is_dirty[x][y] == 1:
            self.is_dirty[x][y] = 0 
            self.cleaned_cells += 1

        if not(self.is_board_clean) and self.cleaned_cells == self.dirty_cells:
            self.finish_time = self.t
            self.is_board_clean = True

    
    def setup(self):
        
        self.dirty_cells = math.ceil(self.p.n * self.p.m * (self.p.percentage_dirty / 100))
        self.is_dirty = self.generateDirtyCells()
        
        self.random_agents = ap.AgentList(self, self.p.random_agents, RandomAgent)
        self.sergio_agents = ap.AgentList(self, self.p.sergio_agents, SergioAgent)
        self.rodrigo_agents = ap.AgentList(self, self.p.rodrigo_agents, RodrigoAgent)
        self.oscar_agents = ap.AgentList(self, self.p.oscar_agents, OscarAgent)
        self.pepe_agents = ap.AgentList(self, self.p.pepe_agents, PepeAgent)
        self.hector_agents = ap.AgentList(self, self.p.hector_agents, HectorAgent)
        

        # self.all_agents = self.sergio_agents + self.rodrigo_agents + self.oscar_agents + self.pepe_agents + self.hector_agents
        self.all_agents = self.random_agents + self.sergio_agents + self.rodrigo_agents + self.oscar_agents + self.pepe_agents + self.hector_agents
        # Genera matriz donde isDirty[i][j] == 1 si la celda en la fila i y columna j esta sucia
        
        # Inicializamos la matriz con ceros
        agentCountMatrix = [[0 for _ in range(self.p.m)] for _ in range(self.p.n)]
        agentCountMatrix[0][0] = len(self.all_agents)
        
        # Variables para generar estadisticas
        self.total_moves = 0
        self.cleaned_cells = 0
        self.is_board_clean = True if self.p.percentage_dirty == 0 else False # Es falso a menos que no haya celdas sucias
        self.finish_time = self.p.steps + 1 # Por default no termina en tiempo


    def step(self):
        self.all_agents.move()

    def update(self):
        """
        self.record('Gini Coefficient (all_agents)', gini(self.all_agents.wealth))
    """

    def end(self):
        time_taken = self.finish_time
        cleaned_percentage = (self.cleaned_cells / (self.dirty_cells)) * 100
        clean_percentage = ((self.p.n * self.p.m - self.dirty_cells + self.cleaned_cells) / (self.p.n * self.p.m)) * 100
        
        
        # print()
        # if not self.is_board_clean:
        #     print("La limpieza no acabo, se llego al tiempo maximo")
        # else:
        #     print(f"Tiempo de limpieza: {time_taken} pasos")
            
        # print(f"Porcentaje de celdas limpiadas: {cleaned_percentage:.2f}%")
        # print(f"Porcentaje de celdas limpias: {clean_percentage:.2f}%")
        # print(f"Total de movimientos: {self.total_moves}")
        
        self.report('total_moves', self.total_moves)
        self.report('clean_percentage', clean_percentage)
        self.report('cleaned_percentage', cleaned_percentage)
        self.report('time_taken', self.finish_time)

In [124]:
parameters = {
    'random_agents': 0,
    'sergio_agents': 0,
    'rodrigo_agents': 0,
    'oscar_agents': 10,
    'pepe_agents': 0,
    'hector_agents': 0,
    'steps': 500,
    'n': 50,
    'm': 50,
    'percentage_dirty': 100,
    'initial_position': (0, 0),
    # 'seed': 22,
}

In [125]:
# agent_types = [ 
#                 # 'sergio_agents',
#                 # 'rodrigo_agents',
#                 'oscar_agents',
#                 # 'pepe_agents'
#                 # 'hector_agents'
#                 ]

# # Por ahora son al azar, podemos definirlos manualmente si es que resulta conveniente
# simulations = 30
# ns = np.random.choice(range(1, 50), simulations)
# ms = np.random.choice(range(1, 50), simulations)
# ks = np.random.choice(range(1, 100), simulations)
# dirty_percents = np.random.choice(range(1, 100), simulations)
# tmaxs = list()
# for i in range(simulations):
#     # At least 2 seconds per cell, to allow some time to finish
#     cells = ns[i] + ms[i]
#     cells *= 2
#     tmaxs.append(np.random.choice(range(cells, cells*10)))

# runs = {}
# for agent_type in agent_types: 
#     curr_runs = {
#         'A': 0,
#         'B': 0,
#         'C': 0,
#         'D': 0,
#         'total': 0
#     }
#     for i in range(simulations):
#         parameters[agent_type] = int(ks[i])
#         parameters['n'] = int(ms[i])
#         parameters['m'] = int(ns[i])
#         parameters['steps'] = int(tmaxs[i])
#         parameters['percentage_dirty'] = int(dirty_percents[i])
#         model = CleaningModel(parameters)
#         results = model.run()
#         reports = results.reporters.loc[0]
        
#         curr_runs['total'] += 1
        
#         # time_taken / total_time
#         percentage_time_taken = reports['time_taken'] / int(tmaxs[i]) 
        
#         if reports['clean_percentage'] >= 100:
#             if percentage_time_taken <= .25:
#                 curr_runs['A'] += 1
#             if percentage_time_taken <= .50:
#                 curr_runs['B'] += 1
#             if percentage_time_taken <= .75:
#                 curr_runs['C'] += 1
#             if percentage_time_taken <= 1.00:
#                 curr_runs['D'] += 1
        
    
#     runs[agent_type] = curr_runs


# print(runs)
    

In [129]:
def animation_plot(model, ax):
    # White: Clean, Black: Dirty, Red: Agent
    color_dict = {0:'#FFFFFF', 1:'#000000', 2:'#FF0000'}
    ndarray_doubles = np.array(model.is_dirty, dtype=float)
    
    for agent in model.all_agents:
        x, y = agent.position
        ndarray_doubles[x][y] = 2
        
    ap.gridplot(ndarray_doubles, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Cleaning model \n Time-step: {model.t}")
    
fig, ax = plt.subplots()
model = CleaningModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml())

In [127]:
# model = CleaningModel(parameters)
# results = model.run()

In [128]:
type(results.reporters)
temp = results.reporters.loc[0]
temp['time_taken']

916